In [79]:
!pip install jsonlines

Please see https://github.com/pypa/pip/issues/5599 for advice on fixing the underlying issue.
To avoid this problem you can invoke Python with '-m pip' instead of running pip directly.
Defaulting to user installation because normal site-packages is not writeable


In [87]:
# !pip install jsonlines
import json
import jsonlines

In [92]:
with open('infersent-trees.json','r') as file:
    a = json.load(file)
    text = json.loads(a)

In [93]:
def tokenize_tree(tree, lower):
    return [(word.lower() if lower else word) for word in tree.split() if word not in ('(', ')')]


def load_data(file_path, lower):
    data = []
    with open(file_path) as f:
        for line in f:
            e = json.loads(line)
            new_e = {}
            if e["gold_label"] == '-':
                continue
            new_e["pairID"] = e["pairID"]
            new_e["label"] = e["gold_label"]
            new_e["premise"] = tokenize_tree(e["sentence1_binary_parse"], lower)
            new_e["hypothesis"] = tokenize_tree(e["sentence2_binary_parse"], lower)
            new_e["premise_binary_parse"] = e["sentence1_binary_parse"]
            new_e["hypothesis_binary_parse"] = e["sentence2_binary_parse"]
            data.append(new_e)
    return data

data = load_data('snli_1.0_test.jsonl',True)

In [94]:
p_tree_list = []
h_tree_list = []
for e in text:
    e = json.loads(e)
    p_tree_list.append(e['p_tree'])
    h_tree_list.append(e['h_tree'])

In [95]:
def get_parse(p,p_tree):
    for action in p_tree:
        idx = list(filter(lambda x: action[x] == 1.0, range(len(action))))[0]
#         print(p)
        if len(p) == 1 and p[0]!='(':
            return '(' + p[0] +')'
        w_1 = p[idx]
        w_2 = p[idx + 1]
        p.pop(idx)
        p.pop(idx)
        w_c = '( '+ w_1 +' '+w_2+' )'
        p.insert(idx,w_c)
        if len(p) == 1:
            return p[0]

In [65]:
for elem,p_tree,h_tree in zip(data,p_tree_list,h_tree_list):
    p = elem['premise'].copy()
    h = elem['hypothesis'].copy()
    parsed_p = get_parse(p,p_tree)
    parsed_h = get_parse(h,h_tree)
    print('premise(p) : \n', ' '.join([str(elem) for elem in elem['premise']]))
    print('p parsed: \n', parsed_p)
    print('p ground truth binary parse: \n', elem['premise_binary_parse'])
    print('hypothesis(h) : \n', ' '.join([str(elem) for elem in elem['hypothesis']]))
    print('parsed h: \n', parsed_h)
    print('hypothesis ground truth binary parse: \n', elem['hypothesis_binary_parse'])

premise(p) : 
 this church choir sings to the masses as they sing joyous songs from the book at a church .
p parsed: 
 ( ( ( this church ) ( choir sings ) ) ( ( ( ( ( to the ) ( masses as ) ) ( they ( sing joyous ) ) ) ( songs ( from the ) ) ) ( book ( ( at a ) ( church . ) ) ) ) )
p ground truth binary parse: 
 ( ( This ( church choir ) ) ( ( ( sings ( to ( the masses ) ) ) ( as ( they ( ( sing ( joyous songs ) ) ( from ( ( the book ) ( at ( a church ) ) ) ) ) ) ) ) . ) )
hypothesis(h) : 
 the church has cracks in the ceiling .
parsed h: 
 ( ( ( the church ) ( has cracks ) ) ( ( in the ) ( ceiling . ) ) )
hypothesis ground truth binary parse: 
 ( ( The church ) ( ( has ( cracks ( in ( the ceiling ) ) ) ) . ) )
premise(p) : 
 this church choir sings to the masses as they sing joyous songs from the book at a church .
p parsed: 
 ( ( ( this church ) ( choir sings ) ) ( ( ( ( ( to the ) ( masses as ) ) ( they ( sing joyous ) ) ) ( songs ( from the ) ) ) ( book ( ( at a ) ( church . ) ) ) 

 ( ( ( A ( young boy ) ) ( wearing ( ( ( a ( red shirt ) ) and ) jeans ) ) ) ( ( ( ( stands ( in ( ( the middle ) ( of ( a field ) ) ) ) ) and ) ( ( throws ( a ( toy plane ) ) ) ( in ( the air ) ) ) ) . ) )
hypothesis(h) : 
 a young boy is playing in the field because his mother kicked him out of the house .
parsed h: 
 ( ( ( ( ( a young ) ( boy is ) ) ( ( playing in ) ( the field ) ) ) ( ( ( because his ) ( mother kicked ) ) ( him ( ( out of ) ( the house ) ) ) ) ) . )
hypothesis ground truth binary parse: 
 ( ( A ( young boy ) ) ( ( is ( ( playing ( in ( the field ) ) ) ( because ( ( his mother ) ( ( ( kicked him ) out ) ( of ( the house ) ) ) ) ) ) ) . ) )
premise(p) : 
 a young boy wearing a red shirt and jeans stands in the middle of a field and throws a toy plane in the air .
p parsed: 
 ( ( ( ( ( a young ) ( boy wearing ) ) ( ( a red ) ( shirt and ) ) ) ( ( jeans ( ( stands in ) ( the middle ) ) ) ( ( of a ) ( ( field and ) ( throws a ) ) ) ) ) ( ( ( toy plane ) ( in the ) ) ( a

 the sun breaks through the trees as a child rides a swing .
p parsed: 
 ( ( ( ( the sun ) ( breaks through ) ) ( ( the trees ) ( as a ) ) ) ( ( child rides ) ( a ( swing . ) ) ) )
p ground truth binary parse: 
 ( ( The sun ) ( ( ( breaks ( through ( the trees ) ) ) ( as ( ( a child ) ( rides ( a swing ) ) ) ) ) . ) )
hypothesis(h) : 
 a child rides a swing in the daytime .
parsed h: 
 ( ( ( ( a child ) ( rides a ) ) ( ( swing in ) ( the daytime ) ) ) . )
hypothesis ground truth binary parse: 
 ( ( A child ) ( ( ( rides ( a swing ) ) ( in ( the daytime ) ) ) . ) )
premise(p) : 
 the sun breaks through the trees as a child rides a swing .
p parsed: 
 ( ( ( ( the sun ) ( breaks through ) ) ( ( the trees ) ( as a ) ) ) ( ( child rides ) ( a ( swing . ) ) ) )
p ground truth binary parse: 
 ( ( The sun ) ( ( ( breaks ( through ( the trees ) ) ) ( as ( ( a child ) ( rides ( a swing ) ) ) ) ) . ) )
hypothesis(h) : 
 the child on the swing is a girl .
parsed h: 
 ( ( ( the child ) ( on the ) )

 ( ( ( ( a guy ) ( is going ) ) ( skateboarding today ) ) . )
hypothesis ground truth binary parse: 
 ( ( A guy ) ( ( is ( going ( skateboarding today ) ) ) . ) )
premise(p) : 
 young boy wearing pajamas lying down in bed and sleeping on a colorful striped pillow .
p parsed: 
 ( ( ( ( young boy ) ( wearing pajamas ) ) ( ( lying down ) ( in bed ) ) ) ( ( ( and sleeping ) ( on a ) ) ( ( colorful striped ) ( pillow . ) ) ) )
p ground truth binary parse: 
 ( ( ( Young boy ) ( ( wearing pajamas ) ( ( ( ( lying down ) ( in bed ) ) and ) ( sleeping ( on ( a ( colorful ( striped pillow ) ) ) ) ) ) ) ) . )
hypothesis(h) : 
 a young boy is playing soccer .
parsed h: 
 ( ( ( ( a young ) ( boy is ) ) ( playing soccer ) ) . )
hypothesis ground truth binary parse: 
 ( ( A ( young boy ) ) ( ( is ( playing soccer ) ) . ) )
premise(p) : 
 young boy wearing pajamas lying down in bed and sleeping on a colorful striped pillow .
p parsed: 
 ( ( ( ( young boy ) ( wearing pajamas ) ) ( ( lying down ) ( in be

p ground truth binary parse: 
 ( ( ( A woman ) ( in black ) ) ( ( ( reviews ( a message ) ) ( as ( she ( walks ( to work ) ) ) ) ) . ) )
hypothesis(h) : 
 the woman in black is being fired via text message .
parsed h: 
 ( ( ( the woman ) ( in black ) ) ( ( is being ) ( fired ( ( via text ) ( message . ) ) ) ) )
hypothesis ground truth binary parse: 
 ( ( ( The woman ) ( in black ) ) ( ( is ( being ( fired ( via ( text message ) ) ) ) ) . ) )
premise(p) : 
 a woman in black reviews a message as she walks to work .
p parsed: 
 ( ( ( ( ( a woman ) ( in black ) ) ( ( reviews a ) ( message as ) ) ) ( ( she walks ) ( to work ) ) ) . )
p ground truth binary parse: 
 ( ( ( A woman ) ( in black ) ) ( ( ( reviews ( a message ) ) ( as ( she ( walks ( to work ) ) ) ) ) . ) )
hypothesis(h) : 
 the woman in black has a job .
parsed h: 
 ( ( ( the woman ) ( in black ) ) ( ( has a ) ( job . ) ) )
hypothesis ground truth binary parse: 
 ( ( ( The woman ) ( in black ) ) ( ( has ( a job ) ) . ) )
premise

...

p parsed: 
 ( ( ( ( a young ) ( face-painted boy ) ) ( ( is sucking ) ( his thumb ) ) ) . )
p ground truth binary parse: 
 ( ( A ( young ( face-painted boy ) ) ) ( ( is ( sucking ( his thumb ) ) ) . ) )
hypothesis(h) : 
 the boy has his face painted .
parsed h: 
 ( ( ( ( the boy ) ( has his ) ) ( face painted ) ) . )
hypothesis ground truth binary parse: 
 ( ( The boy ) ( ( has ( ( his face ) painted ) ) . ) )
premise(p) : 
 a young face-painted boy is sucking his thumb .
p parsed: 
 ( ( ( ( a young ) ( face-painted boy ) ) ( ( is sucking ) ( his thumb ) ) ) . )
p ground truth binary parse: 
 ( ( A ( young ( face-painted boy ) ) ) ( ( is ( sucking ( his thumb ) ) ) . ) )
hypothesis(h) : 
 the boy lost his pacifier .
parsed h: 
 ( ( ( the boy ) ( lost his ) ) ( pacifier . ) )
hypothesis ground truth binary parse: 
 ( ( The boy ) ( ( lost ( his pacifier ) ) . ) )
premise(p) : 
 a young face-painted boy is sucking his thumb .
p parsed: 
 ( ( ( ( a young ) ( face-painted boy ) ) ( ( is suc

 ( ( ( happy children ) ( play on ) ) ( scaffolding . ) )
hypothesis ground truth binary parse: 
 ( ( Happy children ) ( ( play ( on scaffolding ) ) . ) )
premise(p) : 
 young children play on scaffolding .
p parsed: 
 ( ( ( young children ) ( play on ) ) ( scaffolding . ) )
p ground truth binary parse: 
 ( ( Young children ) ( ( play ( on scaffolding ) ) . ) )
hypothesis(h) : 
 young men play on scaffolding .
parsed h: 
 ( ( ( young men ) ( play on ) ) ( scaffolding . ) )
hypothesis ground truth binary parse: 
 ( ( Young men ) ( ( play ( on scaffolding ) ) . ) )
premise(p) : 
 young children play on scaffolding .
p parsed: 
 ( ( ( young children ) ( play on ) ) ( scaffolding . ) )
p ground truth binary parse: 
 ( ( Young children ) ( ( play ( on scaffolding ) ) . ) )
hypothesis(h) : 
 young people play on scaffolding .
parsed h: 
 ( ( ( young people ) ( play on ) ) ( scaffolding . ) )
hypothesis ground truth binary parse: 
 ( ( Young people ) ( ( play ( on scaffolding ) ) . ) )
premis

 a skateboard is grinding on a curb with his skateboard .
p parsed: 
 ( ( ( ( a skateboard ) ( is grinding ) ) ( ( ( on a ) ( curb with ) ) ( his skateboard ) ) ) . )
p ground truth binary parse: 
 ( ( A skateboard ) ( ( is ( grinding ( on ( ( a curb ) ( with ( his skateboard ) ) ) ) ) ) . ) )
hypothesis(h) : 
 the curb is dangerous .
parsed h: 
 ( ( ( the curb ) ( is dangerous ) ) . )
hypothesis ground truth binary parse: 
 ( ( The curb ) ( ( is dangerous ) . ) )
premise(p) : 
 a skateboard is grinding on a curb with his skateboard .
p parsed: 
 ( ( ( ( a skateboard ) ( is grinding ) ) ( ( ( on a ) ( curb with ) ) ( his skateboard ) ) ) . )
p ground truth binary parse: 
 ( ( A skateboard ) ( ( is ( grinding ( on ( ( a curb ) ( with ( his skateboard ) ) ) ) ) ) . ) )
hypothesis(h) : 
 the skateboard is grinding .
parsed h: 
 ( ( ( the skateboard ) ( is grinding ) ) . )
hypothesis ground truth binary parse: 
 ( ( The skateboard ) ( ( is grinding ) . ) )
premise(p) : 
 a skateboard is gr

 ( ( The ( small dog ) ) ( ( is ( running ( across ( the lawn ) ) ) ) . ) )
hypothesis(h) : 
 a dog is chasing a ball .
parsed h: 
 ( ( ( ( a dog ) ( is chasing ) ) ( a ball ) ) . )
hypothesis ground truth binary parse: 
 ( ( A dog ) ( ( is ( chasing ( a ball ) ) ) . ) )
premise(p) : 
 the small dog is running across the lawn .
p parsed: 
 ( ( ( ( the small ) ( dog is ) ) ( ( running across ) ( the lawn ) ) ) . )
p ground truth binary parse: 
 ( ( The ( small dog ) ) ( ( is ( running ( across ( the lawn ) ) ) ) . ) )
hypothesis(h) : 
 a cat is running up a tree .
parsed h: 
 ( ( ( a cat ) ( is running ) ) ( ( up a ) ( tree . ) ) )
hypothesis ground truth binary parse: 
 ( ( A cat ) ( ( is ( ( running up ) ( a tree ) ) ) . ) )
premise(p) : 
 the small dog is running across the lawn .
p parsed: 
 ( ( ( ( the small ) ( dog is ) ) ( ( running across ) ( the lawn ) ) ) . )
p ground truth binary parse: 
 ( ( The ( small dog ) ) ( ( is ( running ( across ( the lawn ) ) ) ) . ) )
hypothesis(h)

p ground truth binary parse: 
 ( ( The ( football player ) ) ( ( prepares ( to ( kick ( the ball ) ) ) ) . ) )
hypothesis(h) : 
 a person is playing a sport .
parsed h: 
 ( ( ( ( a person ) ( is playing ) ) ( a sport ) ) . )
hypothesis ground truth binary parse: 
 ( ( A person ) ( ( is ( playing ( a sport ) ) ) . ) )
premise(p) : 
 the football player prepares to kick the ball .
p parsed: 
 ( ( ( ( the football ) ( player prepares ) ) ( ( to kick ) ( the ball ) ) ) . )
p ground truth binary parse: 
 ( ( The ( football player ) ) ( ( prepares ( to ( kick ( the ball ) ) ) ) . ) )
hypothesis(h) : 
 the quarterback is throwing the football .
parsed h: 
 ( ( ( ( the quarterback ) ( is throwing ) ) ( the football ) ) . )
hypothesis ground truth binary parse: 
 ( ( The quarterback ) ( ( is ( throwing ( the football ) ) ) . ) )
premise(p) : 
 the football player prepares to kick the ball .
p parsed: 
 ( ( ( ( the football ) ( player prepares ) ) ( ( to kick ) ( the ball ) ) ) . )
p ground trut

In [85]:
p = data[0]['premise']
p_tree = p_tree_list[0]

In [86]:
p

['this',
 'church',
 'choir',
 'sings',
 'to',
 'the',
 'masses',
 'as',
 'they',
 'sing',
 'joyous',
 'songs',
 'from',
 'the',
 'book',
 'at',
 'a',
 'church',
 '.']

In [49]:
def get_node(name,left=None,right=None):
    node = {'name':name,'left':left,'right':right}
    return node

In [6]:
get_node("p6",right="chair")

{'name': 'p6', 'left': None, 'right': 'chair'}

In [8]:
stack=[]

In [12]:
stack.append('0')

In [17]:
stack.pop()

IndexError: pop from empty list

In [50]:
def get_tree_formation(string):
    stack=[]
    count = 1
#     print(string.split(" "))
    for alpha in list(string.split(" ")):
        if alpha=='(':
            stack.append(alpha)
        elif alpha==')':
            right = stack.pop()
            left = stack.pop()
            d=stack.pop() # removing "("
            parent = "p"+str(count)
            stack.append(get_node(parent,left,right))
            count+=1
        else:
            stack.append(get_node(alpha))
#         print(id,stack)
    return stack
            

In [34]:
tree_formation("( ( ( ( this ( church choir ) ) ( sings to ) ) ( ( ( the masses ) as ) ( ( they sing ) ( joyous songs ) ) ) ) ( ( ( from the ) ( book at ) ) ( ( a church ) . ) ) )")

['(', '(', '(', '(', 'this', '(', 'church', 'choir', ')', ')', '(', 'sings', 'to', ')', ')', '(', '(', '(', 'the', 'masses', ')', 'as', ')', '(', '(', 'they', 'sing', ')', '(', 'joyous', 'songs', ')', ')', ')', ')', '(', '(', '(', 'from', 'the', ')', '(', 'book', 'at', ')', ')', '(', '(', 'a', 'church', ')', '.', ')', ')', ')']
0 ['(']
1 ['(', '(']
2 ['(', '(', '(']
3 ['(', '(', '(', '(']
4 ['(', '(', '(', '(', {'name': 'this', 'left': None, 'right': None}]
5 ['(', '(', '(', '(', {'name': 'this', 'left': None, 'right': None}, '(']
6 ['(', '(', '(', '(', {'name': 'this', 'left': None, 'right': None}, '(', {'name': 'church', 'left': None, 'right': None}]
7 ['(', '(', '(', '(', {'name': 'this', 'left': None, 'right': None}, '(', {'name': 'church', 'left': None, 'right': None}, {'name': 'choir', 'left': None, 'right': None}]
8 ['(', '(', '(', '(', {'name': 'this', 'left': None, 'right': None}, {'name': 'p1', 'left': {'name': 'church', 'left': None, 'right': None}, 'right': {'name': 'choir'

[{'name': 'p18',
  'left': {'name': 'p11',
   'left': {'name': 'p4',
    'left': {'name': 'p2',
     'left': {'name': 'this', 'left': None, 'right': None},
     'right': {'name': 'p1',
      'left': {'name': 'church', 'left': None, 'right': None},
      'right': {'name': 'choir', 'left': None, 'right': None}}},
    'right': {'name': 'p3',
     'left': {'name': 'sings', 'left': None, 'right': None},
     'right': {'name': 'to', 'left': None, 'right': None}}},
   'right': {'name': 'p10',
    'left': {'name': 'p6',
     'left': {'name': 'p5',
      'left': {'name': 'the', 'left': None, 'right': None},
      'right': {'name': 'masses', 'left': None, 'right': None}},
     'right': {'name': 'as', 'left': None, 'right': None}},
    'right': {'name': 'p9',
     'left': {'name': 'p7',
      'left': {'name': 'they', 'left': None, 'right': None},
      'right': {'name': 'sing', 'left': None, 'right': None}},
     'right': {'name': 'p8',
      'left': {'name': 'joyous', 'left': None, 'right': None

In [4]:
c = {'name': 'p18',
  'left': {'name': 'p11',
   'left': {'name': 'p4',
    'left': {'name': 'p2',
     'left': {'name': 'this', 'left': None, 'right': None},
     'right': {'name': 'p1',
      'left': {'name': 'church', 'left': None, 'right': None},
      'right': {'name': 'choir', 'left': None, 'right': None}}},
    'right': {'name': 'p3',
     'left': {'name': 'sings', 'left': None, 'right': None},
     'right': {'name': 'to', 'left': None, 'right': None}}},
   'right': {'name': 'p10',
    'left': {'name': 'p6',
     'left': {'name': 'p5',
      'left': {'name': 'the', 'left': None, 'right': None},
      'right': {'name': 'masses', 'left': None, 'right': None}},
     'right': {'name': 'as', 'left': None, 'right': None}},
    'right': {'name': 'p9',
     'left': {'name': 'p7',
      'left': {'name': 'they', 'left': None, 'right': None},
      'right': {'name': 'sing', 'left': None, 'right': None}},
     'right': {'name': 'p8',
      'left': {'name': 'joyous', 'left': None, 'right': None},
      'right': {'name': 'songs', 'left': None, 'right': None}}}}},
  'right': {'name': 'p17',
   'left': {'name': 'p14',
    'left': {'name': 'p12',
     'left': {'name': 'from', 'left': None, 'right': None},
     'right': {'name': 'the', 'left': None, 'right': None}},
    'right': {'name': 'p13',
     'left': {'name': 'book', 'left': None, 'right': None},
     'right': {'name': 'at', 'left': None, 'right': None}}},
   'right': {'name': 'p16',
    'left': {'name': 'p15',
     'left': {'name': 'a', 'left': None, 'right': None},
     'right': {'name': 'church', 'left': None, 'right': None}},
    'right': {'name': '.', 'left': None, 'right': None}}}}

In [51]:
def maxDepth(node): 
    if node is None: 
        return 0 ;  
  
    else : 
  
        # Compute the depth of each subtree 
        lDepth = maxDepth(node['left']) 
        rDepth = maxDepth(node['right']) 
  
        # Use the larger one 
        if (lDepth > rDepth): 
            return lDepth+1
        else: 
            return rDepth+1

In [52]:
maxDepth(c)

NameError: name 'c' is not defined

In [53]:
def height(node): 
      
    # Base Case : Tree is empty 
    if node is None: 
        return 0 ; 
      
    # If tree is not empty then height = 1 + max of left  
    # height and right heights  
    return 1 + max(height(node['left']) ,height(node['right'])) 
  
# Function to get the diamtere of a binary tree 
def diameter(root): 
      
    # Base Case when tree is empty  
    if root is None: 
        return 0; 
  
    # Get the height of left and right sub-trees 
    lheight = height(root['left']) 
    rheight = height(root['right']) 
  
    # Get the diameter of left and irgh sub-trees 
    ldiameter = diameter(root['left']) 
    rdiameter = diameter(root['right']) 
  
    # Return max of the following tree: 
    # 1) Diameter of left subtree 
    # 2) Diameter of right subtree 
    # 3) Height of left subtree + height of right subtree +1  
    return max(lheight + rheight + 1, max(ldiameter, rdiameter)) 
      

In [54]:
diameter(c)

NameError: name 'c' is not defined

In [55]:
def cog(M,D):
    return M-D//2

In [56]:
print(str(cog(6,10))+' node from the root')

1 node from the root


In [96]:
p_tree_info = []
h_tree_info = []
p_tree_max_depth_info = []
h_tree_max_depth_info = []
p_tree_diameter_info = []
h_tree_diameter_info = []
p_tree_centroid_info = []
h_tree_centroid_info = []

for elem,p_tree,h_tree in zip(data,p_tree_list,h_tree_list):
    p = elem['premise'].copy()
    h = elem['hypothesis'].copy()
    parsed_p = get_parse(p,p_tree)
    parsed_h = get_parse(h,h_tree)
    p_t = get_tree_formation(parsed_p)[0]
    h_t = get_tree_formation(parsed_h)[0]
    p_tree_info.append(p_t)
    h_tree_info.append(h_t)
    p_tree_max_depth_info.append(maxDepth(p_t))
    h_tree_max_depth_info.append(maxDepth(h_t))
    p_tree_diameter_info.append(diameter(p_t))
    h_tree_diameter_info.append(diameter(h_t))
    p_tree_centroid_info.append(cog(maxDepth(p_t),diameter(p_t)))
    h_tree_centroid_info.append(cog(maxDepth(h_t),diameter(h_t)))
print("tree max")
print("premises")
print(p_tree_max_depth_info)
print("hypotheses")
print(h_tree_max_depth_info)

tree max
premises
[7, 7, 6, 7, 7, 7, 6, 6, 6, 5, 5, 6, 5, 5, 5, 5, 5, 5, 6, 6, 6, 8, 7, 7, 5, 5, 5, 5, 5, 5, 6, 6, 6, 5, 7, 7, 4, 4, 4, 6, 6, 6, 7, 7, 7, 5, 5, 7, 7, 7, 7, 7, 6, 6, 6, 6, 7, 7, 6, 8, 8, 6, 5, 5, 5, 4, 4, 4, 4, 4, 4, 5, 5, 5, 6, 6, 6, 8, 7, 8, 11, 11, 10, 6, 6, 6, 8, 8, 8, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 7, 9, 8, 6, 6, 6, 6, 6, 6, 6, 6, 6, 6, 6, 4, 4, 4, 4, 4, 4, 6, 6, 5, 5, 6, 8, 8, 8, 6, 6, 6, 4, 4, 4, 5, 5, 5, 8, 8, 8, 6, 6, 6, 5, 5, 5, 7, 7, 7, 5, 5, 5, 6, 7, 7, 5, 5, 5, 8, 10, 10, 6, 5, 5, 5, 5, 5, 6, 6, 6, 6, 6, 6, 5, 5, 5, 7, 7, 7, 6, 6, 6, 5, 5, 5, 6, 6, 6, 5, 5, 5, 5, 5, 5, 4, 4, 4, 5, 5, 7, 7, 7, 8, 8, 7, 5, 6, 5, 4, 4, 4, 6, 6, 6, 5, 6, 6, 7, 7, 7, 7, 7, 7, 5, 5, 5, 7, 7, 7, 5, 5, 5, 6, 6, 6, 5, 5, 5, 6, 6, 6, 7, 7, 6, 6, 5, 5, 5, 5, 5, 5, 5, 5, 6, 6, 6, 5, 5, 5, 6, 6, 6, 7, 7, 7, 7, 7, 8, 8, 9, 9, 8, 7, 7, 5, 5, 5, 8, 9, 9, 7, 7, 7, 6, 6, 6, 7, 7, 7, 6, 7, 7, 5, 5, 5, 6, 6, 8, 6, 5, 5, 6, 6, 6, 5, 5, 5, 6, 6, 6, 5, 5, 5, 6, 6, 6, 8, 7, 7, 5, 5, 5, 3, 3, 3

In [97]:
p_avg_max = sum(p_tree_max_depth_info)/len(p_tree_max_depth_info)
h_avg_max = sum(h_tree_max_depth_info)/len(h_tree_max_depth_info)
p_avg_depth = sum(p_tree_diameter_info)/len(p_tree_diameter_info)
h_avg_depth = sum(h_tree_diameter_info)/len(h_tree_diameter_info)
p_avg_centroid = sum(p_tree_centroid_info)/len(p_tree_centroid_info)
h_avg_centroid = sum(h_tree_centroid_info)/len(h_tree_centroid_info)

### For the baseline

In [17]:
print(p_avg_max,
h_avg_max,
p_avg_depth,
h_avg_depth,
p_avg_centroid,
h_avg_centroid,sep="\n")

5.830924267100977
4.731270358306189
9.615940553745927
7.577056188925082
1.2878664495114007
1.1835301302931596


### For Infersent + RLSPINN

In [98]:
print(p_avg_max,
h_avg_max,
p_avg_depth,
h_avg_depth,
p_avg_centroid,
h_avg_centroid,sep="\n")

6.132939739413681
4.6639861563517915
9.191571661237784
6.788578990228013
1.7699511400651466
1.5044788273615635


### SNLI_ Test (Ground Truth)


In [101]:

p_tree_info = []
h_tree_info = []
p_tree_max_depth_info = []
h_tree_max_depth_info = []
p_tree_diameter_info = []
h_tree_diameter_info = []
p_tree_centroid_info = []
h_tree_centroid_info = []

for elem in data:
    p = elem['premise_binary_parse']
    h = elem['hypothesis_binary_parse']
#     parsed_p = get_parse(p,p_tree)
#     parsed_h = get_parse(h,h_tree)
#     print(parsed_p)
    p_t = get_tree_formation(p)[0]
    h_t = get_tree_formation(h)[0]
    p_tree_info.append(p_t)
    h_tree_info.append(h_t)
    p_tree_max_depth_info.append(maxDepth(p_t))
    h_tree_max_depth_info.append(maxDepth(h_t))
    p_tree_diameter_info.append(diameter(p_t))
    h_tree_diameter_info.append(diameter(h_t))
    p_tree_centroid_info.append(cog(maxDepth(p_t),diameter(p_t)))
    h_tree_centroid_info.append(cog(maxDepth(h_t),diameter(h_t)))
print("tree max")
print("premises")
print(p_tree_max_depth_info)
print("hypotheses")
print(h_tree_max_depth_info)


tree max
premises
[11, 11, 11, 10, 10, 10, 8, 8, 8, 8, 8, 8, 8, 8, 8, 7, 7, 7, 7, 7, 7, 11, 11, 11, 8, 8, 8, 7, 7, 7, 10, 10, 10, 9, 9, 9, 6, 6, 6, 13, 13, 13, 8, 8, 8, 6, 6, 10, 10, 10, 8, 8, 8, 11, 11, 11, 13, 13, 13, 9, 9, 9, 8, 8, 8, 6, 6, 6, 6, 6, 6, 7, 7, 7, 9, 9, 9, 10, 10, 10, 15, 15, 15, 10, 10, 10, 9, 9, 9, 8, 8, 8, 9, 9, 9, 7, 7, 7, 6, 6, 6, 13, 13, 13, 13, 13, 9, 9, 9, 6, 6, 6, 12, 12, 12, 5, 5, 5, 5, 5, 5, 10, 10, 7, 7, 7, 9, 9, 9, 9, 9, 9, 5, 5, 5, 8, 8, 8, 14, 14, 14, 7, 7, 7, 6, 6, 6, 11, 11, 11, 10, 10, 10, 9, 9, 9, 10, 10, 10, 12, 12, 12, 9, 9, 9, 5, 5, 5, 8, 8, 8, 9, 9, 9, 8, 8, 8, 10, 10, 10, 11, 11, 11, 6, 6, 6, 10, 10, 10, 5, 5, 5, 6, 6, 6, 7, 7, 7, 7, 7, 10, 10, 10, 12, 12, 12, 8, 8, 8, 7, 7, 7, 8, 8, 8, 9, 9, 9, 12, 12, 12, 8, 8, 8, 6, 6, 6, 11, 11, 11, 8, 8, 8, 10, 10, 10, 6, 6, 6, 6, 6, 6, 10, 10, 10, 8, 8, 8, 9, 9, 9, 6, 6, 6, 9, 9, 9, 7, 7, 7, 7, 7, 7, 9, 9, 9, 9, 9, 9, 10, 10, 10, 8, 8, 8, 7, 7, 7, 11, 11, 11, 10, 10, 10, 6, 6, 6, 7, 7, 7, 10, 10, 10, 6, 6,

In [102]:
p_avg_max = sum(p_tree_max_depth_info)/len(p_tree_max_depth_info)
h_avg_max = sum(h_tree_max_depth_info)/len(h_tree_max_depth_info)
p_avg_depth = sum(p_tree_diameter_info)/len(p_tree_diameter_info)
h_avg_depth = sum(h_tree_diameter_info)/len(h_tree_diameter_info)
p_avg_centroid = sum(p_tree_centroid_info)/len(p_tree_centroid_info)
h_avg_centroid = sum(h_tree_centroid_info)/len(h_tree_centroid_info)
print(p_avg_max,
h_avg_max,
p_avg_depth,
h_avg_depth,
p_avg_centroid,
h_avg_centroid,sep="\n")

8.974653908794789
6.389352605863192
12.476995114006515
8.531657166123779
2.9903298045602607
2.370114006514658


In [1]:
from binarytree import Node

ModuleNotFoundError: No module named 'binarytree'

In [26]:
from binarytree import Node

In [27]:
def get_node_v(name,left=None,right=None):
    p = Node(name)
    p.left = left
    p.right = right
    return p

In [28]:
def get_tree_formation_v(string):
    stack=[]
    chars = {}
    count = 1
#     print(string.split(" "))
    for alpha in list(string.split(" ")):
        if alpha=='(':
            stack.append(alpha)
        elif alpha==')':
            right = stack.pop()
            left = stack.pop()
            d=stack.pop() # removing "("
            parent = count
            stack.append(get_node_v(parent,left,right))
            count+=1
        else:
            chars[count] = alpha
            stack.append(get_node_v(count))
            count+=1
#         print(id,stack)
    
    return stack,chars

### Baseline

In [29]:
string1 = "( ( ( ( this ( church choir ) ) ( sings to ) ) ( ( ( the masses ) as ) ( ( they sing ) ( joyous songs ) ) ) ) ( ( ( from the ) ( book at ) ) ( ( a church ) . ) ) )"

In [30]:
tree,chars = get_tree_formation_v(string1)

In [32]:
pprint(chars)

{1: 'this',
 2: 'church',
 3: 'choir',
 6: 'sings',
 7: 'to',
 10: 'the',
 11: 'masses',
 13: 'as',
 15: 'they',
 16: 'sing',
 18: 'joyous',
 19: 'songs',
 24: 'from',
 25: 'the',
 27: 'book',
 28: 'at',
 31: 'a',
 32: 'church',
 34: '.'}


In [34]:
print(tree[0])


                    ________________________________________37_____________________
                   /                                                               \
            ______23_______________                                       __________36_________
           /                       \                                     /                     \
    ______9__                   ____22_________                     ____30___               ____35
   /         \                 /               \                   /         \             /      \
  5__         8           ____14            ____21___            _26         _29         _33       34
 /   \       / \         /      \          /         \          /   \       /   \       /   \
1     4     6   7      _12       13      _17         _20       24    25    27    28    31    32
     / \              /   \             /   \       /   \
    2   3            10    11          15    16    18    19



In [31]:
from pprint import pprint

In [5]:
pprint(c)

{'left': {'left': {'left': {'left': {'left': None,
                                     'name': 'this',
                                     'right': None},
                            'name': 'p2',
                            'right': {'left': {'left': None,
                                               'name': 'church',
                                               'right': None},
                                      'name': 'p1',
                                      'right': {'left': None,
                                                'name': 'choir',
                                                'right': None}}},
                   'name': 'p4',
                   'right': {'left': {'left': None,
                                      'name': 'sings',
                                      'right': None},
                             'name': 'p3',
                             'right': {'left': None,
                                       'name': 'to',
                        

### Infersent + RLSPINN

In [38]:
string2 = "( ( ( this church ) ( choir sings ) ) ( ( ( ( ( to the ) ( masses as ) ) ( they ( sing joyous ) ) ) ( songs ( from the ) ) ) ( book ( ( at a ) ( church . ) ) ) ) )"

In [39]:
tree,chars = get_tree_formation_v(string2)

In [41]:
pprint(chars)

{1: 'this',
 2: 'church',
 4: 'choir',
 5: 'sings',
 8: 'to',
 9: 'the',
 11: 'masses',
 12: 'as',
 15: 'they',
 16: 'sing',
 17: 'joyous',
 21: 'songs',
 22: 'from',
 23: 'the',
 27: 'book',
 28: 'at',
 29: 'a',
 31: 'church',
 32: '.'}


In [40]:
print(tree[0])


        ______37_______________________________________________________
       /                                                               \
    __7__                                               ________________36___
   /     \                                             /                     \
  3       6                           ________________26___                  _35_________
 / \     / \                         /                     \                /            \
1   2   4   5             __________20___                  _25___          27         ____34___
                         /               \                /      \                   /         \
                     ___14___            _19___          21      _24               _30         _33
                    /        \          /      \                /   \             /   \       /   \
                   10        _13       15      _18             22    23          28    29    31    32
                  /  \

### Ground Truth

In [103]:
string3 = "( ( This ( church choir ) ) ( ( ( sings ( to ( the masses ) ) ) ( as ( they ( ( sing ( joyous songs ) ) ( from ( ( the book ) ( at ( a church ) ) ) ) ) ) ) ) . ) )"

In [105]:
tree,chars = get_tree_formation_v(string3)

In [106]:
pprint(chars)

{1: '',
 2: 'This',
 3: 'church',
 4: 'choir',
 7: 'sings',
 8: 'to',
 9: 'the',
 10: 'masses',
 14: 'as',
 15: 'they',
 16: 'sing',
 17: 'joyous',
 18: 'songs',
 21: 'from',
 22: 'the',
 23: 'book',
 25: 'at',
 26: 'a',
 27: 'church',
 36: '.'}


In [107]:
print(tree[0])


1

